### Creating an AST from Python Source

In [1]:
import ast
my_tree = ast.parse("3 + 4*x")
print(ast.dump(my_tree))
print(type(my_tree))

Module(body=[Expr(value=BinOp(left=Constant(value=3), op=Add(), right=BinOp(left=Constant(value=4), op=Mult(), right=Name(id='x', ctx=Load()))))], type_ignores=[])
<class 'ast.Module'>


### Multiline Source

In [2]:
source = '''
fruits = ['grapes', 'mango']
name = 'peter'

for fruit in fruits:
    print(f'{name} likes {fruit}')
'''
my_tree = ast.parse(source)
print(ast.dump(my_tree))

Module(body=[Assign(targets=[Name(id='fruits', ctx=Store())], value=List(elts=[Constant(value='grapes'), Constant(value='mango')], ctx=Load())), Assign(targets=[Name(id='name', ctx=Store())], value=Constant(value='peter')), For(target=Name(id='fruit', ctx=Store()), iter=Name(id='fruits', ctx=Load()), body=[Expr(value=Call(func=Name(id='print', ctx=Load()), args=[JoinedStr(values=[FormattedValue(value=Name(id='name', ctx=Load()), conversion=-1), Constant(value=' likes '), FormattedValue(value=Name(id='fruit', ctx=Load()), conversion=-1)])], keywords=[]))], orelse=[])], type_ignores=[])


### Traverse AST

In [3]:
import ast

class NodePrinter(ast.NodeVisitor):
    def generic_visit(self, node):
        print(node)
        super().generic_visit(node) #DO NOT FORGET, OTHERWISE THE CHILDREN NODES WILL NOT BE VISITED RECURESIVELY


source = '''
fruits = ['grapes', 'mango']
name = 'peter'

for fruit in fruits:
    print(f'{name} likes {fruit}')
'''

my_ast = ast.parse(source)

node_printer = NodePrinter()
node_printer.visit(my_ast)


In [4]:
import ast

class StringRead(ast.NodeVisitor):
    
    def visit_Constant(self, node):
        print(f'{node.value}')
        

source = '''
fruits = ['grapes', 'mango']
name = 'peter'

for fruit in fruits:
    print(name + ' likes ' + fruit)
'''

my_ast = ast.parse(source)
#my_ast = ast.parse(open("peter.py", "r").read())

node_printer = StringRead()
node_printer.visit(my_ast)


grapes
mango
peter
 likes 


### From AST to Python String

In [5]:
source = '''
fruits = ['grapes', 'mango']
name = 'peter'

for fruit in fruits:
    print(name + ' likes ' + fruit)
'''
my_ast = ast.parse(source)

recons = ast.unparse(my_ast)
print(recons)

fruits = ['grapes', 'mango']
name = 'peter'
for fruit in fruits:
    print(name + ' likes ' + fruit)


### Modify Python Source Code

In [6]:
import ast

class StringReplace(ast.NodeTransformer):
    
    def visit_Constant(self, node):
        #print(f'{node.value}')
        node.value = node.value.upper() if isinstance(node.value, str) else node.value
        return node
        

source = '''
fruits = ['grapes', 'mango']
name = 'peter'

for fruit in fruits:
    print(name + ' likes ' + fruit)
'''

org_ast = ast.parse(source)
mod_ast = ast.parse(source)
#my_ast = ast.parse(open("peter.py", "r").read())

node_printer = StringReplace()
node_printer.visit(mod_ast)

recons = ast.unparse(mod_ast)
print("Modified Source: ")
print(recons)

Modified Source: 
fruits = ['GRAPES', 'MANGO']
name = 'PETER'
for fruit in fruits:
    print(name + ' LIKES ' + fruit)


In [7]:
exec(compile(org_ast, filename="", mode="exec"))

peter likes grapes
peter likes mango


In [8]:
exec(compile(mod_ast, filename="", mode="exec"))

PETER LIKES GRAPES
PETER LIKES MANGO


In [9]:
class Marvel(ast.NodeTransformer):
    
    def visit_Constant(self, node):
        if isinstance(node.value, str):           
            node.value = node.value.replace("peter", "Peter Parker")
        return node


source = '''
fruits = ['grapes', 'mango']
name = 'peter'

for fruit in fruits:
    print(name + ' likes ' + fruit)
'''

org_ast = ast.parse(source)
#exec(compile(org_ast, filename = "", mode="exec"))

mod_ast = ast.parse(source)
Marvel().visit(mod_ast)
print("Modified: ")
print(ast.unparse(mod_ast))
print("-"*80)

Modified: 
fruits = ['grapes', 'mango']
name = 'Peter Parker'
for fruit in fruits:
    print(name + ' likes ' + fruit)
--------------------------------------------------------------------------------


In [10]:
exec(compile(mod_ast, filename="", mode="exec"))

Peter Parker likes grapes
Peter Parker likes mango


In [11]:
class PlusEdit(ast.NodeTransformer):
    
    def visit_BinOp(self, node):
        super().generic_visit(node)
        return ast.BinOp(
            left = node.left,
            op = ast.Sub(),
            right = node.right
        )
        
    
source = '''
a = 1 + 4 + 5
b = 2 + 3 + a
c = a + b + (a-b)
print(c)
'''

org_ast = ast.parse(source)
#exec(compile(org_ast, filename = "", mode="exec"))

mod_ast = ast.parse(source)
PlusEdit().visit(mod_ast)
print("Modified: ")
print(ast.unparse(mod_ast))
print("-"*80)

Modified: 
a = 1 - 4 - 5
b = 2 - 3 - a
c = a - b - (a - b)
print(c)
--------------------------------------------------------------------------------


In [12]:
### Loop Body Modifier

In [13]:
#ast.dump(ast.parse("print('xxx')").body[0].value)

In [14]:
class LoopEditor(ast.NodeTransformer):
    
    
    def visit_For(self, node):
        super().generic_visit(node)
        
        ib = ast.parse("print('Iteration Begin')").body[0]
        ie = ast.parse("print('Iteration End  ')").body[0]
        """
        loop_node = ast.For(
            target = node.target,
            iter = node.iter,
            body = new_body,
            orelse = node.orelse,
            type_comment = node.type_comment
        )
        """
        #print("New Loop")
        node.body = [ib] + node.body + [ie]
        return node

    
source = '''
n = 3
for i in range(n):
    print(f"Current value of i is {i}")
'''

org_ast = ast.parse(source)
#exec(compile(org_ast, filename = "", mode="exec"))

mod_ast = ast.parse(source)
LoopEditor().visit(mod_ast)
ast.fix_missing_locations(mod_ast)
print("-"*80)
print("Modified: ")
print(ast.unparse(mod_ast))
print("-"*80)

exec(compile(mod_ast, filename = "", mode="exec"))

--------------------------------------------------------------------------------
Modified: 
n = 3
for i in range(n):
    print('Iteration Begin')
    print(f'Current value of i is {i}')
    print('Iteration End  ')
--------------------------------------------------------------------------------
Iteration Begin
Current value of i is 0
Iteration End  
Iteration Begin
Current value of i is 1
Iteration End  
Iteration Begin
Current value of i is 2
Iteration End  
